# Konvolúciós hálózatok - augmentáció és előtanított modellek

In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt

# Keras CNN MNIST

Forrás:

https://keras.io/examples/mnist_cnn/


In [ ]:
from __future__ import print_function
import tensorflow as tf
from tensorflow.keras.datasets import mnist
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, Dropout, Flatten
from tensorflow.keras.layers import Conv2D, MaxPooling2D
from tensorflow.keras import backend as K

In [ ]:
batch_size = 128
num_classes = 10
epochs = 50

# input image dimensions
img_rows, img_cols = 28, 28

# the data, split between train and test sets
(x_train, y_train), (x_test, y_test) = mnist.load_data()

if K.image_data_format() == 'channels_first':
    x_train = x_train.reshape(x_train.shape[0], 1, img_rows, img_cols)
    x_test = x_test.reshape(x_test.shape[0], 1, img_rows, img_cols)
    input_shape = (1, img_rows, img_cols)
else:
    x_train = x_train.reshape(x_train.shape[0], img_rows, img_cols, 1)
    x_test = x_test.reshape(x_test.shape[0], img_rows, img_cols, 1)
    input_shape = (img_rows, img_cols, 1)

x_train = x_train.astype('float32')
x_test = x_test.astype('float32')
x_train /= 255
x_test /= 255
print('x_train shape:', x_train.shape)
print(x_train.shape[0], 'train samples')
print(x_test.shape[0], 'test samples')

# convert class vectors to binary class matrices
y_train = tf.keras.utils.to_categorical(y_train, num_classes)
y_test = tf.keras.utils.to_categorical(y_test, num_classes)

model = Sequential()
model.add(Conv2D(32, kernel_size=(3, 3),
                 activation='relu',
                 input_shape=input_shape))
model.add(Conv2D(64, (3, 3), activation='relu'))
model.add(MaxPooling2D(pool_size=(2, 2)))
model.add(Dropout(0.25))
model.add(Flatten())
model.add(Dense(128, activation='relu'))
model.add(Dropout(0.5))
model.add(Dense(num_classes, activation='softmax'))

model.compile(loss=tf.keras.losses.categorical_crossentropy,
              optimizer=tf.keras.optimizers.Adadelta(),
              metrics=['accuracy'])

model.fit(x_train, y_train,
          batch_size=batch_size,
          epochs=epochs,
          verbose=1,
          validation_data=(x_test, y_test))
score = model.evaluate(x_test, y_test, verbose=0)
print('Test loss:', score[0])
print('Test accuracy:', score[1])

# Cats and dogs

In [ ]:
# Adatok letöltése

!wget --no-check-certificate \
    https://storage.googleapis.com/mledu-datasets/cats_and_dogs_filtered.zip \
    -O /tmp/cats_and_dogs_filtered.zip



In [ ]:
# Kicsomagolás

import os
import zipfile

local_zip = './tmp/cats_and_dogs_filtered.zip'
zip_ref = zipfile.ZipFile(local_zip, 'r')
zip_ref.extractall('./tmp/')
zip_ref.close()

In [ ]:
os.listdir("./tmp/cats_and_dogs_filtered")

In [ ]:
print(os.listdir("./tmp/cats_and_dogs_filtered/train/"))
print(os.listdir("./tmp/cats_and_dogs_filtered/train/cats/"))
print(len(list(os.listdir("./tmp/cats_and_dogs_filtered/train/cats/"))))

In [ ]:
# Augmentálás

#ImageDataGen = tf.keras.preprocessing.image.ImageDataGenerator()

from tensorflow.keras.preprocessing.image import ImageDataGenerator, array_to_img, img_to_array, load_img

train_datagen = ImageDataGenerator(
    rescale=1./255,
    shear_range=0.2,
    zoom_range=0.2,
    horizontal_flip=True)

test_datagen = ImageDataGenerator(rescale=1./255)

train_generator = train_datagen.flow_from_directory(
    'tmp/cats_and_dogs_filtered/train',
    target_size=(150, 150),
    batch_size=32,
    class_mode='binary')

validation_generator = test_datagen.flow_from_directory(
    'tmp/cats_and_dogs_filtered/validation',
    target_size=(150, 150),
    batch_size=32,
    class_mode='binary')

In [ ]:
#train_datagen.flow(train_generator)  #  ()
#next(train_generator)
next_batch = train_generator.next()

In [ ]:
for i in range(5):
    plt.figure()
    plt.imshow(next_batch[0][i,:,:,:])

In [ ]:
img_cat_1 = load_img("tmp/cats_and_dogs_filtered/train/cats/cat.0.jpg")
array_img_cat_1 = img_to_array(img_cat_1)  # this is a Numpy array with shape (374, 500, 3)
array_img_cat_1 = array_img_cat_1.reshape((1,) + array_img_cat_1.shape)  # this is a Numpy array with shape (1, 374, 500, 3)

In [ ]:
i = 0
for batch in train_datagen.flow(array_img_cat_1):
    plt.figure()
    plt.imshow(batch[0,:,:,:])
    i += 1
    if i > 3:
        break

Kész hálózatok használata

In [ ]:
vgg_model = tf.keras.applications.vgg16.VGG16(include_top=False, weights=None,
                                              input_tensor=None, input_shape=None, pooling=None, classes=1000)

In [ ]:
x = vgg_model.output
x = tf.keras.layers.GlobalAveragePooling2D()(x)
# let's add a fully-connected layer
x = tf.keras.layers.Dense(1024, activation='relu')(x)

predictions = tf.keras.layers.Dense(len(train_generator.class_indices), activation='softmax')(x)

# this is the model we will train
model = tf.keras.models.Model(inputs=vgg_model.input, outputs=predictions)

for layer in vgg_model.layers:
    layer.trainable = True


model.compile(optimizer='rmsprop', loss='categorical_crossentropy',
              metrics=['acc'])

model.summary()

In [ ]:
history = model.fit_generator(train_generator,
                              epochs=epochs,
                              steps_per_epoch=round(train_generator.n / batch_size),
                              validation_data=validation_generator,
                              validation_steps=round(validation_generator.n / batch_size),)



In [ ]:

hist = pd.DataFrame(history.history)
hist['epoch'] = history.epoch
print(hist.tail())

def plot_history(history):
    plt.figure()
    plt.xlabel('Epoch')
    plt.ylabel('loss and val_loss')
    plt.plot(hist['epoch'], hist['loss'], label='loss')
    plt.plot(hist['epoch'], hist['val_loss'], label = 'val_loss')
    plt.legend()
    plt.ylim([(min(hist['loss'].min(), hist['val_loss'].min()))*0.9,
              (max(hist['loss'].max(), hist['val_loss'].max()))*1.1])


    plt.figure()
    plt.xlabel('Epoch')
    plt.ylabel('Accuracy')
    plt.plot(hist['epoch'], hist['accuracy'],
           label='Accuracy')
    plt.plot(hist['epoch'], hist['val_accuracy'],
           label = 'Validation Accuracy')
    plt.legend()
    plt.ylim([(min(hist['accuracy'].min(), hist['val_accuracy'].min()))*0.9,
              (max(hist['accuracy'].max(), hist['val_accuracy'].max()))*1.1])




plot_history(history)

